In [1]:
import pandas as pd

# Display the complete contents of dataframe cells.
pd.set_option("display.max_colwidth", None)

In [2]:

import os
from getpass import getpass

import openai

if not (openai_api_key := os.getenv("OPENAI_API_KEY")):
    openai_api_key = getpass("🔑 Enter your OpenAI API key: ")
openai.api_key = openai_api_key
os.environ["OPENAI_API_KEY"] = openai_api_key

In [3]:

import phoenix as px
from llama_index.core import set_global_handler
from phoenix.trace.langchain import LangChainInstrumentor

session = px.launch_app()

# Setup instrumentation for both llama-index and LangChain (used by Ragas)
set_global_handler("arize_phoenix")
LangChainInstrumentor().instrument()

🌍 To view the Phoenix app in your browser, visit http://localhost:6006/
📺 To view the Phoenix app in a notebook, run `px.active_session().view()`
📖 For more information on how to use Phoenix, check out https://docs.arize.com/phoenix


In [4]:
from llama_index.core import SimpleDirectoryReader

dir_path = "./data/prompt-engineering-papers"
reader = SimpleDirectoryReader(dir_path, num_files_limit=2)
documents = reader.load_data()

In [6]:
from phoenix.trace import using_project
from ragas.testset.evolutions import multi_context, reasoning, simple
from ragas.testset.generator import TestsetGenerator, RunConfig

TEST_SIZE = 10

# generator with openai models
generator = TestsetGenerator.with_openai(
    generator_llm="gpt-3.5-turbo-0125",
    critic_llm="gpt-3.5-turbo-0125",
    embeddings="text-embedding-3-large",
)

# set question type distribution
distribution = {simple: 0.5, reasoning: 0.25, multi_context: 0.25}

# disable async and change config to keep from reaching OpenAI rate limits
with using_project("ragas-testset"):
    testset = generator.generate_with_llamaindex_docs(
        documents, test_size=TEST_SIZE, distributions=distribution,
        run_config=RunConfig(
            timeout=60,
            max_retries=10,
            max_wait = 180, # default: 60
            max_workers= 1, # default: 16 
    ),
    raise_exceptions=False,
    is_async=False,
    )
test_df = testset.to_pandas()
test_df.head()

/tmp/ipykernel_92261/1452519360.py:8: DeprecationWarning: The function with_openai was deprecated in 0.1.4, and will be removed in the 0.2.0 release. Use from_langchain instead.
  generator = TestsetGenerator.with_openai(


embedding nodes:   0%|          | 0/144 [00:00<?, ?it/s]

Filename and doc_id are the same for all nodes.


Generating:   0%|          | 0/10 [00:00<?, ?it/s]

max retries exceeded for ReasoningEvolution(generator_llm=LangchainLLMWrapper(run_config=RunConfig(timeout=60, max_retries=10, max_wait=180, max_workers=1, exception_types=<class 'openai.RateLimitError'>)), docstore=InMemoryDocumentStore(splitter=<langchain_text_splitters.base.TokenTextSplitter object at 0x7fb70fd61240>, nodes=[Node(page_content='arXiv:1605.08386v1  [math.CO]  26 May 2016HEAT-BATH RANDOM WALKS WITH MARKOV BASES\nCAPRICE STANLEY AND TOBIAS WINDISCH\nAbstract. Graphs on lattice points are studied whose edges come from a ﬁ nite set of\nallowed moves of arbitrary length. We show that the diameter of these graphs on ﬁbers of a\nﬁxed integer matrix can be bounded from above by a constant. W e then study the mixing\nbehaviour of heat-bath random walks on these graphs. We also state explicit conditions\non the set of moves so that the heat-bath random walk, a genera lization of the Glauber\ndynamics, is an expander in ﬁxed dimension.\nContents\n1. Introduction 1\n2. Graphs and

question  \
0                         How is a scoring LM used in the two-stage retrieval method proposed by Rubin et al. for selecting demonstrations?   
1                                                          What is discussed in the survey on Geometric Random Walks by Santosh S. Vempala?   
2                                                               What is the role of memory-of-thoughts in enabling ChatGPT to self-improve?   
3  How do models like Frozen, Flamingo, and METALM demonstrate the capability of few-shot learning in the context of vision-language tasks?   
4                                            How are heat-bath random walks related to Markov bases in the context of finite subsets of Zd?   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       contexts  \
0                                                    

In [7]:
my_traces = px.Client().get_trace_dataset().save(directory="./data")

AttributeError: 'NoneType' object has no attribute 'save'

In [ ]:
my_traces.hex